# Prepare 准备工作

In [1]:
import numpy as np # 数据处理最重要的模块
import pandas as pd # 数据处理最重要的模块

from IPython.core.interactiveshell import InteractiveShell # jupyter运行输出的模块

#显示每一个运行结果
InteractiveShell.ast_node_interactivity = 'all'

#设置行不限制数量
#pd.set_option('display.max_rows',None)

#设置列不限制数量
pd.set_option('display.max_columns', None)


# Import Data 导入数据

In [2]:
%%time
data = pd.read_csv('datasets/000001.csv')
data['Day'] = pd.to_datetime(data['Day'],format='%Y/%m/%d')
data.set_index('Day', inplace = True)
data.sort_values(by = ['Day'],axis=0, ascending=True)
data

CPU times: total: 0 ns
Wall time: 140 ms


Preclose       Open    Highest     Lowest      Close  \
Day                                                                 
1990-12-19               96.0500    99.9800    95.7900    99.9800   
1990-12-20      99.98   104.3000   104.3900    99.9800   104.3900   
1990-12-21     104.39   109.0700   109.1300   103.7300   109.1300   
1990-12-24     109.13   113.5700   114.5500   109.1300   114.5500   
1990-12-25     114.55   120.0900   120.2500   114.5500   120.2500   
...               ...        ...        ...        ...        ...   
2024-07-25  2901.9518  2891.8918  2897.7674  2872.8497  2886.7416   
2024-07-26  2886.7416  2885.9953  2899.1162  2875.3959  2890.8973   
2024-07-29  2890.8973  2889.4726  2898.9512  2878.5825  2891.8453   
2024-07-30  2891.8453  2885.2152  2885.2152  2865.1493  2879.2996   
2024-07-31  2879.2996  2877.5409  2940.5927  2876.3009  2938.7493   

                 Volume         Money  
Day                                    
1990-12-19       126000  4.940000e+05  
1990-12-20        19700  8.400000e+04  
1990-12-21         2800  1.600000e+04  
1990-12-24         3200  3.100000e+04  
1990-12-25         1500  6.000000e+03  
...                 ...           ...  
2024-07-25  27463950000  2.732820e+11  
2024-07-26  27838753600  2.754430e+11  
2024-07-29  25689972700  2.600950e+11  
2024-07-30  26247883700  2.694770e+11  
2024-07-31  41272341700  4.188720e+11  

[8210 rows x 7 columns]

# 计算收益率 Calculate Return

股票的收益率的计算一般使用的是 **收盘价** 来计算。


* Raw Return: $R_t = \frac{p_t - p_{t-1}}{p_{t-1}} $
* Log Return: $r_t = log(p_t) - log(p_{t-1})$

自然对数收益率与原始收益率的关系：

$r_t = log(1 + R_t)$

* 在实际数据中，我们常用收盘价来计算收益率。为什么？
* 对数收益率和原始收益率的区别在哪里？分别用在什么样的场景呢？

## 复利的计算
设某资产的的初始值为 $C$, 名义上的年利率为 $r$ ， 但是在一年内分成 $m$ 次付息，理论上每次付息 $C \frac{r}{m}$, 最终的资产净值应为 

$C+C \frac{r}{m} \times m=C(1+r)$; 

但是，因为提前付息，所以提前支付的利息也进入账户增值，从第二次付息开始，支付的利息就超过了 $C \frac{r}{m}$, 使得一年后的净值要高于 $C(1+r)$。 一年后的净值为

$C\left(1+\frac{r}{m}\right)^{m}$

当 $m \rightarrow \infty$ 时，由极限 $\lim _{x \rightarrow+\infty}\left(1+\frac{1}{x}\right)^{x}=e$, 可知

$\lim _{m \rightarrow \infty} C\left(1+\frac{r}{m}\right)^{m}=\lim _{m \rightarrow \infty} C\left[\left(1+\frac{r}{m}\right)^{\frac{m}{r}}\right]^{r}=C e^{r}$

这时 $r$ 称为连续复利， 它也对应某个时间单位（一般是年)， $R=e^{r}-1$ 是连续复利 $r$ 对应的实际利率, $r$ 与 $R$ 的关系为

$R=e^{r}-1, \quad r=\ln (1+R)$

In [5]:
data_new = data['1995-01':'2024-07'].copy()
data_new['Close'] = pd.to_numeric(data_new['Close'])
data_new['Preclose'] = pd.to_numeric(data_new['Preclose'])
data_new

Preclose       Open    Highest     Lowest      Close  \
Day                                                                 
1995-01-03   647.8700   637.7200   647.7100   630.5300   639.8800   
1995-01-04   639.8800   641.9000   655.5100   638.8600   653.8100   
1995-01-05   653.8100   655.3800   657.5200   645.8100   646.8900   
1995-01-06   646.8900   642.7500   643.8900   636.3300   640.7600   
1995-01-09   640.7600   637.5200   637.5500   625.0400   626.0000   
...               ...        ...        ...        ...        ...   
2024-07-25  2901.9518  2891.8918  2897.7674  2872.8497  2886.7416   
2024-07-26  2886.7416  2885.9953  2899.1162  2875.3959  2890.8973   
2024-07-29  2890.8973  2889.4726  2898.9512  2878.5825  2891.8453   
2024-07-30  2891.8453  2885.2152  2885.2152  2865.1493  2879.2996   
2024-07-31  2879.2996  2877.5409  2940.5927  2876.3009  2938.7493   

                 Volume         Money  
Day                                    
1995-01-03     23451800  1.806930e+08  
1995-01-04     42222000  3.069230e+08  
1995-01-05     43012300  3.015330e+08  
1995-01-06     48748200  3.537580e+08  
1995-01-09     50985100  3.985190e+08  
...                 ...           ...  
2024-07-25  27463950000  2.732820e+11  
2024-07-26  27838753600  2.754430e+11  
2024-07-29  25689972700  2.600950e+11  
2024-07-30  26247883700  2.694770e+11  
2024-07-31  41272341700  4.188720e+11  

[7182 rows x 7 columns]

In [6]:
# 计算000001上证指数日收益率 两种：
data_new['Raw_return'] = data_new['Close'] / data_new['Preclose'] - 1
data_new['Log_return'] = np.log(data_new['Close']) - np.log(data_new['Preclose'])
data_new['Stupid_return'] = 0
data_new

Preclose       Open    Highest     Lowest      Close  \
Day                                                                 
1995-01-03   647.8700   637.7200   647.7100   630.5300   639.8800   
1995-01-04   639.8800   641.9000   655.5100   638.8600   653.8100   
1995-01-05   653.8100   655.3800   657.5200   645.8100   646.8900   
1995-01-06   646.8900   642.7500   643.8900   636.3300   640.7600   
1995-01-09   640.7600   637.5200   637.5500   625.0400   626.0000   
...               ...        ...        ...        ...        ...   
2024-07-25  2901.9518  2891.8918  2897.7674  2872.8497  2886.7416   
2024-07-26  2886.7416  2885.9953  2899.1162  2875.3959  2890.8973   
2024-07-29  2890.8973  2889.4726  2898.9512  2878.5825  2891.8453   
2024-07-30  2891.8453  2885.2152  2885.2152  2865.1493  2879.2996   
2024-07-31  2879.2996  2877.5409  2940.5927  2876.3009  2938.7493   

                 Volume         Money  Raw_return  Log_return  Stupid_return  
Day                                                                           
1995-01-03     23451800  1.806930e+08   -0.012333   -0.012409              0  
1995-01-04     42222000  3.069230e+08    0.021770    0.021536              0  
1995-01-05     43012300  3.015330e+08   -0.010584   -0.010641              0  
1995-01-06     48748200  3.537580e+08   -0.009476   -0.009521              0  
1995-01-09     50985100  3.985190e+08   -0.023035   -0.023305              0  
...                 ...           ...         ...         ...            ...  
2024-07-25  27463950000  2.732820e+11   -0.005241   -0.005255              0  
2024-07-26  27838753600  2.754430e+11    0.001440    0.001439              0  
2024-07-29  25689972700  2.600950e+11    0.000328    0.000328              0  
2024-07-30  26247883700  2.694770e+11   -0.004338   -0.004348              0  
2024-07-31  41272341700  4.188720e+11    0.020647    0.020437              0  

[7182 rows x 10 columns]

* 注意下面代码的运行，Python靠缩进来判断代码的级别，注意使用。
* 能不用for while等循环就少用

In [17]:
for i in range(1,len(data_new)):
    data_new['Stupid_return'][i] = (data_new['Close'][i] - data_new['Preclose'][i]) / data_new['Preclose'][i]

data_new

C:\Users\cheng\AppData\Local\Temp\ipykernel_400\573994191.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  data_new['Stupid_return'][i] = (data_new['Close'][i] - data_new['Preclose'][i]) / data_new['Preclose'][i]
C:\Users\cheng\AppData\Local\Temp\ipykernel_400\573994191.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_new['Stupid_return'][i] = (data_new['Close'][i] - data_new['Preclose'][i]) / data_new['Preclose'][i]
C:\Users\cheng\AppData\Local\Temp\ipykernel_400\573994191.py:2: FutureWarning: Series.__setitem__ treating keys as positions is deprecated. In a future version, integer keys will always be trea

Preclose       Open    Highest     Lowest      Close  \
Day                                                                 
1995-01-03   647.8700   637.7200   647.7100   630.5300   639.8800   
1995-01-04   639.8800   641.9000   655.5100   638.8600   653.8100   
1995-01-05   653.8100   655.3800   657.5200   645.8100   646.8900   
1995-01-06   646.8900   642.7500   643.8900   636.3300   640.7600   
1995-01-09   640.7600   637.5200   637.5500   625.0400   626.0000   
...               ...        ...        ...        ...        ...   
2024-07-25  2901.9518  2891.8918  2897.7674  2872.8497  2886.7416   
2024-07-26  2886.7416  2885.9953  2899.1162  2875.3959  2890.8973   
2024-07-29  2890.8973  2889.4726  2898.9512  2878.5825  2891.8453   
2024-07-30  2891.8453  2885.2152  2885.2152  2865.1493  2879.2996   
2024-07-31  2879.2996  2877.5409  2940.5927  2876.3009  2938.7493   

                 Volume         Money  Raw_return  Log_return  Stupid_return  \
Day                                                                            
1995-01-03     23451800  1.806930e+08   -0.012333   -0.012409      -0.012333   
1995-01-04     42222000  3.069230e+08    0.021770    0.021536       0.021770   
1995-01-05     43012300  3.015330e+08   -0.010584   -0.010641      -0.010584   
1995-01-06     48748200  3.537580e+08   -0.009476   -0.009521      -0.009476   
1995-01-09     50985100  3.985190e+08   -0.023035   -0.023305      -0.023035   
...                 ...           ...         ...         ...            ...   
2024-07-25  27463950000  2.732820e+11   -0.005241   -0.005255      -0.005241   
2024-07-26  27838753600  2.754430e+11    0.001440    0.001439       0.001440   
2024-07-29  25689972700  2.600950e+11    0.000328    0.000328       0.000328   
2024-07-30  26247883700  2.694770e+11   -0.004338   -0.004348      -0.004338   
2024-07-31  41272341700  4.188720e+11    0.020647    0.020437       0.020647   

            delta_return  
Day                       
1995-01-03  7.667910e-05  
1995-01-04  2.335762e-04  
1995-01-05  5.641013e-05  
1995-01-06  4.518399e-05  
1995-01-09  2.694550e-04  
...                  ...  
2024-07-25  1.378416e-05  
2024-07-26  1.035204e-06  
2024-07-29  5.375594e-08  
2024-07-30  9.437740e-06  
2024-07-31  2.102657e-04  

[7182 rows x 11 columns]

In [7]:
for i in range(0,7182):
    data_new.iloc[i,9] = data_new.iloc[i,4] / data_new.iloc[i,0] - 1

data_new

C:\Users\cheng\AppData\Local\Temp\ipykernel_400\4204191076.py:2: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '-0.01233272107058514' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  data_new.iloc[i,9] = data_new.iloc[i,4] / data_new.iloc[i,0] - 1


Preclose       Open    Highest     Lowest      Close  \
Day                                                                 
1995-01-03   647.8700   637.7200   647.7100   630.5300   639.8800   
1995-01-04   639.8800   641.9000   655.5100   638.8600   653.8100   
1995-01-05   653.8100   655.3800   657.5200   645.8100   646.8900   
1995-01-06   646.8900   642.7500   643.8900   636.3300   640.7600   
1995-01-09   640.7600   637.5200   637.5500   625.0400   626.0000   
...               ...        ...        ...        ...        ...   
2024-07-25  2901.9518  2891.8918  2897.7674  2872.8497  2886.7416   
2024-07-26  2886.7416  2885.9953  2899.1162  2875.3959  2890.8973   
2024-07-29  2890.8973  2889.4726  2898.9512  2878.5825  2891.8453   
2024-07-30  2891.8453  2885.2152  2885.2152  2865.1493  2879.2996   
2024-07-31  2879.2996  2877.5409  2940.5927  2876.3009  2938.7493   

                 Volume         Money  Raw_return  Log_return  Stupid_return  
Day                                                                           
1995-01-03     23451800  1.806930e+08   -0.012333   -0.012409      -0.012333  
1995-01-04     42222000  3.069230e+08    0.021770    0.021536       0.021770  
1995-01-05     43012300  3.015330e+08   -0.010584   -0.010641      -0.010584  
1995-01-06     48748200  3.537580e+08   -0.009476   -0.009521      -0.009476  
1995-01-09     50985100  3.985190e+08   -0.023035   -0.023305      -0.023035  
...                 ...           ...         ...         ...            ...  
2024-07-25  27463950000  2.732820e+11   -0.005241   -0.005255      -0.005241  
2024-07-26  27838753600  2.754430e+11    0.001440    0.001439       0.001440  
2024-07-29  25689972700  2.600950e+11    0.000328    0.000328       0.000328  
2024-07-30  26247883700  2.694770e+11   -0.004338   -0.004348      -0.004338  
2024-07-31  41272341700  4.188720e+11    0.020647    0.020437       0.020647  

[7182 rows x 10 columns]

In [8]:
# 两种计算方式的差
data_new['delta_return'] = data_new['Raw_return'] - data_new['Log_return']
print('平均来看，两种方式计算的收益率之间的区别为:',np.mean(data_new['delta_return'])*100,"%")

平均来看，两种方式计算的收益率之间的区别为: 0.01348426816744191 %


# 计算月、季和年度收益率 Calculate Monthly Quarterly and Yearly Return


## 月度收益率
$t$ 月的收益率使用该月月末的收盘价 和 上个月$t - 1$月末的收盘价来计算

* Raw Return: $R_t = \frac{p_t - p_{t-1}}{p_{t-1}} $
* Log Return: $r_t = log(p_t) - log(p_{t-1})$

### 使用resample函数

#### 对数回报率求和

In [10]:
Month_data = data_new.resample('ME')['Log_return'].sum().to_frame() # R语言非常常见
Month_data['Raw_Return'] = np.exp(Month_data['Log_return']) - 1
Month_data

Log_return  Raw_Return
Day                               
1995-01-31   -0.141139   -0.131631
1995-02-28   -0.023979   -0.023694
1995-03-31    0.163651    0.177803
1995-04-30   -0.109315   -0.103552
1995-05-31    0.188901    0.207922
...                ...         ...
2024-03-31    0.008585    0.008622
2024-04-30    0.020716    0.020932
2024-05-31   -0.005818   -0.005801
2024-06-30   -0.039452   -0.038684
2024-07-31   -0.009703   -0.009656

[355 rows x 2 columns]

#### 取月末的价格计算

In [11]:
Month_data = data_new.resample('m')['Close'].last().to_frame()
Month_data['Preclose'] = Month_data['Close'].shift(1)
Month_data['Log_return'] = np.log(Month_data['Close']) - np.log(Month_data['Preclose'])
Month_data

C:\Users\cheng\AppData\Local\Temp\ipykernel_400\2521873696.py:1: FutureWarning: 'm' is deprecated and will be removed in a future version, please use 'ME' instead.
  Month_data = data_new.resample('m')['Close'].last().to_frame()


Close   Preclose  Log_return
Day                                         
1995-01-31   562.5900        NaN         NaN
1995-02-28   549.2600   562.5900   -0.023979
1995-03-31   646.9200   549.2600    0.163651
1995-04-30   579.9300   646.9200   -0.109315
1995-05-31   700.5100   579.9300    0.188901
...               ...        ...         ...
2024-03-31  3041.1669  3015.1712    0.008585
2024-04-30  3104.8245  3041.1669    0.020716
2024-05-31  3086.8134  3104.8245   -0.005818
2024-06-30  2967.4028  3086.8134   -0.039452
2024-07-31  2938.7493  2967.4028   -0.009703

[355 rows x 3 columns]

### 使用groupby函数

In [12]:
# “1990-12-12”日期格式 里面的year年份 month月份 day 直接提出取来
data_new2 = data_new.copy()
data_new2['year'] = data_new2.index.year
data_new2['month'] = data_new2.index.month
data_new2
# 使用的时间、日期格式提取 字符串提出的方式 前四个字符当作年份 6-7字符是月份 提取出来的是字符串 变成数值

Preclose       Open    Highest     Lowest      Close  \
Day                                                                 
1995-01-03   647.8700   637.7200   647.7100   630.5300   639.8800   
1995-01-04   639.8800   641.9000   655.5100   638.8600   653.8100   
1995-01-05   653.8100   655.3800   657.5200   645.8100   646.8900   
1995-01-06   646.8900   642.7500   643.8900   636.3300   640.7600   
1995-01-09   640.7600   637.5200   637.5500   625.0400   626.0000   
...               ...        ...        ...        ...        ...   
2024-07-25  2901.9518  2891.8918  2897.7674  2872.8497  2886.7416   
2024-07-26  2886.7416  2885.9953  2899.1162  2875.3959  2890.8973   
2024-07-29  2890.8973  2889.4726  2898.9512  2878.5825  2891.8453   
2024-07-30  2891.8453  2885.2152  2885.2152  2865.1493  2879.2996   
2024-07-31  2879.2996  2877.5409  2940.5927  2876.3009  2938.7493   

                 Volume         Money  Raw_return  Log_return  Stupid_return  \
Day                                                                            
1995-01-03     23451800  1.806930e+08   -0.012333   -0.012409      -0.012333   
1995-01-04     42222000  3.069230e+08    0.021770    0.021536       0.021770   
1995-01-05     43012300  3.015330e+08   -0.010584   -0.010641      -0.010584   
1995-01-06     48748200  3.537580e+08   -0.009476   -0.009521      -0.009476   
1995-01-09     50985100  3.985190e+08   -0.023035   -0.023305      -0.023035   
...                 ...           ...         ...         ...            ...   
2024-07-25  27463950000  2.732820e+11   -0.005241   -0.005255      -0.005241   
2024-07-26  27838753600  2.754430e+11    0.001440    0.001439       0.001440   
2024-07-29  25689972700  2.600950e+11    0.000328    0.000328       0.000328   
2024-07-30  26247883700  2.694770e+11   -0.004338   -0.004348      -0.004338   
2024-07-31  41272341700  4.188720e+11    0.020647    0.020437       0.020647   

            delta_return  year  month  
Day                                    
1995-01-03  7.667910e-05  1995      1  
1995-01-04  2.335762e-04  1995      1  
1995-01-05  5.641013e-05  1995      1  
1995-01-06  4.518399e-05  1995      1  
1995-01-09  2.694550e-04  1995      1  
...                  ...   ...    ...  
2024-07-25  1.378416e-05  2024      7  
2024-07-26  1.035204e-06  2024      7  
2024-07-29  5.375594e-08  2024      7  
2024-07-30  9.437740e-06  2024      7  
2024-07-31  2.102657e-04  2024      7  

[7182 rows x 13 columns]

In [13]:
Month_data2 = data_new2.groupby(['year','month'])['Log_return'].sum().to_frame()
Month_data2

Log_return
year month            
1995 1       -0.141139
     2       -0.023979
     3        0.163651
     4       -0.109315
     5        0.188901
...                ...
2024 3        0.008585
     4        0.020716
     5       -0.005818
     6       -0.039452
     7       -0.009703

[355 rows x 1 columns]

In [14]:

Month_data2 = pd.DataFrame(
    data_new2.groupby(['year', 'month'])['Log_return'].apply(lambda x: sum(x)))
# sum函数是python内置函数 自己去写函数 function名 chenghang
# Month_data2 = pd.DataFrame(data_new2.groupby(['year','month'])['Log_return'].sum())
Month_data2

Log_return
year month            
1995 1       -0.141139
     2       -0.023979
     3        0.163651
     4       -0.109315
     5        0.188901
...                ...
2024 3        0.008585
     4        0.020716
     5       -0.005818
     6       -0.039452
     7       -0.009703

[355 rows x 1 columns]